In [1]:
import pandas as pd
import numpy as np
import re
from re import sub
import multiprocessing

from gensim.models.phrases import Phrases, Phraser
from gensim.models import Word2Vec
from gensim.test.utils import get_tmpfile
from gensim.models import KeyedVectors


from time import time 
from collections import defaultdict

import logging  # Setting up the loggings to monitor gensim
logging.basicConfig(format="%(levelname)s - %(asctime)s: %(message)s", datefmt= '%H:%M:%S', level=logging.INFO)

In [2]:
import pandas as pd
import nltk
from bs4 import BeautifulSoup
from nltk import word_tokenize, FreqDist
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk import sent_tokenize
from re import sub
from gensim.models.phrases import Phrases, Phraser
from gensim.models import Word2Vec
from time import time  # To time our operations
from collections import defaultdict  # For word frequency
import tensorflow as tf

import spacy  # For preprocessing

import logging  # Setting up the loggings to monitor gensim
logging.basicConfig(format="%(levelname)s - %(asctime)s: %(message)s", datefmt= '%H:%M:%S', level=logging.INFO)

In [3]:
df=pd.read_csv('./sw1.csv')
df2=pd.read_csv('./sw2.csv')
df3=pd.read_csv('./sw3.csv')
df4=pd.read_csv('./sw4.csv')
df5=pd.read_csv('./sw5.csv')
df6=pd.read_csv('./sw6.csv')
df7=pd.read_csv('./sw7.csv')
df8=pd.read_csv('./sw8.csv')
df9=pd.read_csv('./sw9.csv')


In [4]:
frames = [df, df2, df3, df4, df5, df6, df7, df8, df9]

In [5]:
df = pd.concat(frames)

In [6]:
df

audience-reviews__review
0                                10x better then the ST
1     i'm only giving it this many stars because of ...
2     No Star Wars movie falls below the 7/10 thresh...
3     Still a better love story than twilight and st...
4     music is so good the fight at the and too 10 t...
...                                                 ...
1005  I loved the story line. And it wasn't predicta...
1006  Valiant effort in trying to correct the course...
1007                           Not mad about the ending
1008                           Amazing ending to it all
1009  I thought it was a great way to end the saga. ...

[9250 rows x 1 columns]

In [6]:
df['reviews'] = df['audience-reviews__review']
df=df.drop(columns=['audience-reviews__review'])

In [7]:
df

reviews
0                                10x better then the ST
1     i'm only giving it this many stars because of ...
2     No Star Wars movie falls below the 7/10 thresh...
3     Still a better love story than twilight and st...
4     music is so good the fight at the and too 10 t...
...                                                 ...
1005  I loved the story line. And it wasn't predicta...
1006  Valiant effort in trying to correct the course...
1007                           Not mad about the ending
1008                           Amazing ending to it all
1009  I thought it was a great way to end the saga. ...

[9250 rows x 1 columns]

In [8]:
text=df['reviews']

In [9]:
text= df['reviews'].to_list()

In [9]:
text= " ".join(text)


In [10]:
text

'10x better then the ST i\'m only giving it this many stars because of the music and the darth maul fight. No Star Wars movie falls below the 7/10 threshold, but this one came close! Still a better love story than twilight and still a better plot that Last Jedi. music is so good the fight at the and too 10 times better then the disney triology Maybe it was the decades of anticipation. Perhaps we just expected magic. The truth is, this isn\'t an awful movie. But neither is it good. Best to just skip and re-watch the original trilogy again. Perhaps in hindsight, jumping back into film making after a 10 year hiatus and attempting to make one of the most highly anticipated films ever, wasn\'t such a great idea.  The film is confusing and boring. And truly unwatchable. The plot of the film once you can finally figure out what is supposed to be going on is actually quite good.  But the screenplay, acting and execution is very very bad. This movie is hated on way too much. It has one of the b

In [11]:
text = text.lower()

In [17]:
words = []
for word in text.split():
    if word != '.': # because we don't want to treat . as a word
        words.append(word)
words = set(words) # so that all duplicate words are removed
word2int = {}
int2word = {}
vocab_size = len(words) # gives the total number of unique words
for i,word in enumerate(words):
    word2int[word] = i
    int2word[i] = word

In [18]:
words

{'nightmares',
 'racer',
 'experiences',
 'apaixonado',
 '7',
 'juxtaposed',
 'forest',
 'choppy',
 'mini',
 'heritage',
 'directory',
 'aarrgh',
 'mask',
 'deviated',
 'bomber',
 'locator',
 'boosts',
 'inespressivit',
 'stylized',
 'exceptions',
 'city',
 'tell',
 'money',
 'secrets',
 'officer',
 'revert',
 'disgusted',
 'devistating',
 'hopefully',
 'sized',
 'charged',
 'laura',
 'permanently',
 'narrativi',
 'huger',
 'aweful',
 'memorabilia',
 'knightly',
 'here',
 'hungery',
 'contiene',
 'childbirth',
 'constructed',
 'hubiera',
 'cinephiles',
 'dieses',
 'inconsistencies',
 'missions',
 'bearded',
 'nessuno',
 'labeled',
 'travesty',
 'veinte',
 'misfortune',
 '15',
 'wins',
 'superbly',
 'context',
 'surname',
 'instances',
 'smuggler',
 'abandoned',
 'topics',
 'lgama',
 'do',
 'wistful',
 'booooooooooooooooriiiiiiiing',
 'getting',
 'displaying',
 'comercial',
 'fells',
 'vor',
 'bond',
 'puppy',
 'tryna',
 'point',
 '23',
 'poetically',
 'proclaims',
 'bight',
 'pessimist

In [19]:
raw_sentences = text.split('.')
sentences = []
for sentence in raw_sentences:
    sentences.append(sentence.split())

In [20]:
sentences

[['10x',
  'better',
  'then',
  'the',
  'st',
  'i',
  'm',
  'only',
  'giving',
  'it',
  'this',
  'many',
  'stars',
  'because',
  'of',
  'the',
  'music',
  'and',
  'the',
  'darth',
  'maul',
  'fight',
  'no',
  'star',
  'wars',
  'movie',
  'falls',
  'below',
  'the',
  '7/10',
  'threshold',
  'but',
  'this',
  'one',
  'came',
  'close',
  '!',
  'still',
  'a',
  'better',
  'love',
  'story',
  'than',
  'twilight',
  'and',
  'still',
  'a',
  'better',
  'plot',
  'that',
  'last',
  'jedi',
  'music',
  'is',
  'so',
  'good',
  'the',
  'fight',
  'at',
  'the',
  'and',
  'too',
  '10',
  'times',
  'better',
  'then',
  'the',
  'disney',
  'triology',
  'maybe',
  'it',
  'was',
  'the',
  'decades',
  'of',
  'anticipation',
  'perhaps',
  'we',
  'just',
  'expected',
  'magic',
  'the',
  'truth',
  'is',
  'this',
  'isn',
  't',
  'an',
  'awful',
  'movie',
  'but',
  'neither',
  'is',
  'it',
  'good',
  'best',
  'to',
  'just',
  'skip',
  'and',
  

In [14]:
text

'10x better then the st i\'m only giving it this many stars because of the music and the darth maul fight. no star wars movie falls below the 7/10 threshold, but this one came close! still a better love story than twilight and still a better plot that last jedi. music is so good the fight at the and too 10 times better then the disney triology maybe it was the decades of anticipation. perhaps we just expected magic. the truth is, this isn\'t an awful movie. but neither is it good. best to just skip and re-watch the original trilogy again. perhaps in hindsight, jumping back into film making after a 10 year hiatus and attempting to make one of the most highly anticipated films ever, wasn\'t such a great idea.  the film is confusing and boring. and truly unwatchable. the plot of the film once you can finally figure out what is supposed to be going on is actually quite good.  but the screenplay, acting and execution is very very bad. this movie is hated on way too much. it has one of the b

In [14]:
# code inspired by rafaljanwojcik 
def text_to_word_list(text):
    ''' Pre process and convert texts to a list of words 
    method inspired by method from eliorc github repo: https://github.com/eliorc/Medium/blob/master/MaLSTM.ipynb'''
  
    text = str(text)
    text = text.lower()
    # Clean the text
    text = sub(r"[^A-Za-z0-9^,!?.\/'+]", " ", text)
    text = sub(r"\+", " plus ", text)
    text = sub(r",", " ", text)
    text = sub(r"\.", " ", text)
    text = sub(r"!", " ! ", text)
    text = sub(r"\?", " ? ", text)
    text = sub(r"'", " ", text)
    text = sub(r":", " : ", text)
    text = sub(r"\s{2,}", " ", text)

    return text

In [15]:
text= text_to_word_list(text)

In [16]:
text

'10x better then the st i m only giving it this many stars because of the music and the darth maul fight no star wars movie falls below the 7/10 threshold but this one came close ! still a better love story than twilight and still a better plot that last jedi music is so good the fight at the and too 10 times better then the disney triology maybe it was the decades of anticipation perhaps we just expected magic the truth is this isn t an awful movie but neither is it good best to just skip and re watch the original trilogy again perhaps in hindsight jumping back into film making after a 10 year hiatus and attempting to make one of the most highly anticipated films ever wasn t such a great idea the film is confusing and boring and truly unwatchable the plot of the film once you can finally figure out what is supposed to be going on is actually quite good but the screenplay acting and execution is very very bad this movie is hated on way too much it has one of the best star wars soundtra

In [15]:
tf=text

In [19]:
tf

' 10x better then the st i m only giving it this many stars because of the music and the darth maul fight no star wars movie falls below the 7/10 threshold but this one came close ! still a better love story than twilight and still a better plot that last jedi music is so good the fight at the and too 10 times better then the disney triology maybe it was the decades of anticipation perhaps we just expected magic the truth is this isn t an awful movie but neither is it good best to just skip and re watch the original trilogy again perhaps in hindsight jumping back into film making after a 10 year hiatus and attempting to make one of the most highly anticipated films ever wasn t such a great idea the film is confusing and boring and truly unwatchable the plot of the film once you can finally figure out what is supposed to be going on is actually quite good but the screenplay acting and execution is very very bad this movie is hated on way too much it has one of the best star wars soundtr

In [16]:
sent = [row for row in tf]
phrases = Phrases(sent, min_count=1, progress_per=50000)
bigram = Phraser(phrases)
sentences = bigram[sent]
sentences[0]

INFO - 16:29:42: collecting all words and their counts
INFO - 16:29:42: PROGRESS: at sentence #0, processed 0 words and 0 word types
INFO - 16:29:42: PROGRESS: at sentence #50000, processed 50000 words and 40 word types
INFO - 16:29:42: PROGRESS: at sentence #100000, processed 100000 words and 40 word types
INFO - 16:29:42: PROGRESS: at sentence #150000, processed 150000 words and 40 word types
INFO - 16:29:42: PROGRESS: at sentence #200000, processed 200000 words and 40 word types
INFO - 16:29:42: PROGRESS: at sentence #250000, processed 250000 words and 41 word types
INFO - 16:29:42: PROGRESS: at sentence #300000, processed 300000 words and 41 word types
INFO - 16:29:42: PROGRESS: at sentence #350000, processed 350000 words and 41 word types
INFO - 16:29:42: PROGRESS: at sentence #400000, processed 400000 words and 41 word types
INFO - 16:29:42: PROGRESS: at sentence #450000, processed 450000 words and 41 word types
INFO - 16:29:42: PROGRESS: at sentence #500000, processed 500000 wor

'1'

In [21]:
sentences

[['10x',
  'better',
  'then',
  'the',
  'st',
  'i',
  'm',
  'only',
  'giving',
  'it',
  'this',
  'many',
  'stars',
  'because',
  'of',
  'the',
  'music',
  'and',
  'the',
  'darth',
  'maul',
  'fight',
  'no',
  'star',
  'wars',
  'movie',
  'falls',
  'below',
  'the',
  '7/10',
  'threshold',
  'but',
  'this',
  'one',
  'came',
  'close',
  '!',
  'still',
  'a',
  'better',
  'love',
  'story',
  'than',
  'twilight',
  'and',
  'still',
  'a',
  'better',
  'plot',
  'that',
  'last',
  'jedi',
  'music',
  'is',
  'so',
  'good',
  'the',
  'fight',
  'at',
  'the',
  'and',
  'too',
  '10',
  'times',
  'better',
  'then',
  'the',
  'disney',
  'triology',
  'maybe',
  'it',
  'was',
  'the',
  'decades',
  'of',
  'anticipation',
  'perhaps',
  'we',
  'just',
  'expected',
  'magic',
  'the',
  'truth',
  'is',
  'this',
  'isn',
  't',
  'an',
  'awful',
  'movie',
  'but',
  'neither',
  'is',
  'it',
  'good',
  'best',
  'to',
  'just',
  'skip',
  'and',
  

In [22]:
w2v_model = Word2Vec(min_count=3,
                     window=4,
                     size=300,
                     sample=1e-5, 
                     alpha=0.03, 
                     min_alpha=0.0007, 
                     negative=20,
                     workers=multiprocessing.cpu_count()-1)

start = time()

w2v_model.build_vocab(sentences, progress_per=50000)

print('Time to build vocab: {} mins'.format(round((time() - start) / 60, 2)))

INFO - 16:35:06: collecting all words and their counts
INFO - 16:35:06: PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
INFO - 16:35:07: collected 16185 word types from a corpus of 451501 raw words and 1 sentences
INFO - 16:35:07: Loading a fresh vocabulary
INFO - 16:35:07: effective_min_count=3 retains 6186 unique words (38% of original 16185, drops 9999)
INFO - 16:35:07: effective_min_count=3 leaves 439277 word corpus (97% of original 451501, drops 12224)
INFO - 16:35:07: deleting the raw counts dictionary of 16185 items
INFO - 16:35:07: sample=1e-05 downsamples 2466 most-common words
INFO - 16:35:07: downsampling leaves estimated 75789 word corpus (17.3% of prior 439277)
INFO - 16:35:07: estimated required memory for 6186 words and 300 dimensions: 17939400 bytes
INFO - 16:35:07: resetting layer weights


Time to build vocab: 0.03 mins


In [23]:

start = time()

w2v_model.train(sentences, total_examples=w2v_model.corpus_count, epochs=30, report_delay=1)

print('Time to train the model: {} mins'.format(round((time() - start) / 60, 2)))

w2v_model.init_sims(replace=True)

INFO - 16:35:13: training model with 3 workers on 6186 vocabulary and 300 features, using sg=0 hs=0 sample=1e-05 negative=20 window=4
INFO - 16:35:13: worker thread finished; awaiting finish of 2 more threads
INFO - 16:35:13: worker thread finished; awaiting finish of 1 more threads
INFO - 16:35:13: worker thread finished; awaiting finish of 0 more threads
INFO - 16:35:13: EPOCH - 1 : training on 451501 raw words (10000 effective words) took 0.1s, 92447 effective words/s
INFO - 16:35:13: worker thread finished; awaiting finish of 2 more threads
INFO - 16:35:13: worker thread finished; awaiting finish of 1 more threads
INFO - 16:35:13: worker thread finished; awaiting finish of 0 more threads
INFO - 16:35:13: EPOCH - 2 : training on 451501 raw words (10000 effective words) took 0.1s, 97683 effective words/s
INFO - 16:35:13: worker thread finished; awaiting finish of 2 more threads
INFO - 16:35:13: worker thread finished; awaiting finish of 1 more threads
INFO - 16:35:13: worker thread f

INFO - 16:35:16: EPOCH - 24 : training on 451501 raw words (10000 effective words) took 0.1s, 93040 effective words/s
INFO - 16:35:16: worker thread finished; awaiting finish of 2 more threads
INFO - 16:35:16: worker thread finished; awaiting finish of 1 more threads
INFO - 16:35:16: worker thread finished; awaiting finish of 0 more threads
INFO - 16:35:16: EPOCH - 25 : training on 451501 raw words (10000 effective words) took 0.1s, 77249 effective words/s
INFO - 16:35:16: worker thread finished; awaiting finish of 2 more threads
INFO - 16:35:16: worker thread finished; awaiting finish of 1 more threads
INFO - 16:35:16: worker thread finished; awaiting finish of 0 more threads
INFO - 16:35:16: EPOCH - 26 : training on 451501 raw words (10000 effective words) took 0.1s, 69768 effective words/s
INFO - 16:35:16: worker thread finished; awaiting finish of 2 more threads
INFO - 16:35:16: worker thread finished; awaiting finish of 1 more threads
INFO - 16:35:16: worker thread finished; await

Time to train the model: 0.06 mins


In [24]:
w2v_model.save("word2vec.model")

INFO - 16:35:30: saving Word2Vec object under word2vec.model, separately None
INFO - 16:35:30: not storing attribute vectors_norm
INFO - 16:35:30: not storing attribute cum_table
INFO - 16:35:31: saved word2vec.model


In [25]:
w2v_model

NameError: name 'KMeans' is not defined